In [1]:
import os
import json
import pandas as pd
import configparser

In [2]:
import boto3
from botocore.exceptions import ClientError

In [3]:
# Create a ConfigParser object
config = configparser.ConfigParser()

# Read the INI file
config.read('.secrets_auth.ini')
section_name = "AWS auth"

aws_access_key_id = config.get(section_name, "ACCESS_KEY")
aws_secret_access_key = config.get(section_name, "SECRET_KEY")


In [4]:
# Use this code snippet in your app.
# If you need more information about configurations
# or implementing the sample code, visit the AWS docs:
# https://aws.amazon.com/developer/language/python/

import boto3
from botocore.exceptions import ClientError


def get_secret():

    secret_name = "demo/alberto-rivas"
    region_name = "us-west-2"

    # Create a Secrets Manager client
    session = boto3.session.Session(
        aws_access_key_id=aws_access_key_id,
        aws_secret_access_key=aws_secret_access_key
    )
    client = session.client(
        service_name='secretsmanager',
        region_name=region_name
    )

    try:
        get_secret_value_response = client.get_secret_value(
            SecretId=secret_name
        )
        return json.loads(get_secret_value_response['SecretString'])
        
    except ClientError as e:
        # For a list of exceptions thrown, see
        # https://docs.aws.amazon.com/secretsmanager/latest/apireference/API_GetSecretValue.html
        raise e
        

In [5]:
def get_dataframe(workbook_id, worksheet_id):
    workbench_url = f"https://develop.seeq.dev/workbook/{workbook_id}/worksheet/{worksheet_id}"
    df = spy.pull(workbench_url)
    return df
    

In [6]:
def process_get_items_request(passed_args):
    if not "workbook_id" in passed_args:
        return pd.DataFrame({"Error code": ["422"], "Error message": ["workbook_id parameter missing"]})
    if not "worksheet_id" in passed_args:
        return pd.DataFrame({"Error code": ["422"], "Error message": ["worksheet_id parameter missing"]})
    
    workbook_id = passed_args['workbook_id']
    worksheet_id = passed_args['worksheet_id']
    return  get_dataframe(workbook_id, worksheet_id)

In [7]:
def upload_data(passed_args):
    if not 'file_name' in passed_args:
        return "Server error 422, file_name parameter missing"

    process_get_items_request(passed_args)
    file_name = passed_args['file_name']
    df = process_get_items_request(REQUEST['args'])

    try:
        secrets = get_secret()
        response = df.to_csv(
            f"s3://{secrets['AWS_S3_BUCKET']}/{file_name}",
            index=True,
            storage_options={
                "key": secrets['AWS_ACCESS_KEY_ID'],
                "secret": secrets['AWS_SECRET_ACCESS_KEY'],
            },
        )
        return "Success: Data has been uploaded"
    except Exception as e:
        return str(e)

In [8]:
def download_data(passed_args):
    if not 'file_name' in passed_args:
        return pd.DataFrame({"Error code": ["422"], "Error message": ["file_name parameter missing"]}).to_json(orient="index")

    file_name = passed_args['file_name']


    try:
        secrets = get_secret()
        df = pd.read_csv(f"s3://{secrets['AWS_S3_BUCKET']}/{file_name}",
                         index_col=0,
                         storage_options={
                             "key": secrets['AWS_ACCESS_KEY_ID'],
                             "secret": secrets['AWS_SECRET_ACCESS_KEY']
                         }
                        )
        return df.to_json(orient="index")
    except Exception as e:
        return pd.DataFrame({"Error": [str(e)], "Error message": [f"unable to download data from s3://{secrets['AWS_S3_BUCKET']}/{file_name}"]}).to_json(orient='index')


In [10]:
# GET /worksheet/items

process_get_items_request(REQUEST['args']).to_json(orient="index")

In [1]:
# GET /upload
upload_data(REQUEST['args'])


In [ ]:
# GET /download
download_data(REQUEST['args'])


In [ ]:
# GET /hello
"hello from Data Lab"